In [1]:
def symmetric_power_recursion(psi0,psi1,n):
    chars = [psi0,psi1]
    for i in range(1,n-1):
        chars.append(psi1*chars[i]-chars[i-1])
    return chars

In [2]:
def elliptic_chars_matrix(E,num_chars,SatoTate="SU(2)",max_prime=2^12,prec=32):
    # Given an elliptic curve E/Q, and a number n = num_chars of irreducible
    # characters, compute the nxn inner product matrix with respect to the
    # first n irreducible characters for the Sato-Tate group "SU(2)" or "NU(1)".
    RR = RealField(prec); n = num_chars
    MatRR = MatrixSpace(RR,n,n); A = MatRR(0)
    assert SatoTate in ["SU(2)","NU(1)"], "SatoTate must SU(2) or NU(1)"
    if SatoTate == "SU(2)": psi0 = 1
    if SatoTate == "NU(1)": psi0 = 2
    num = 0
    D = E.discriminant(); bad_primes = D.numerator() * D.denominator()
    for p in primes(max_prime):
        if bad_primes.mod(p) == 0: continue
        Ep = E.base_extend(GF(p))
        ap = Ep.trace_of_frobenius()
        if SatoTate == "NU(1)":
           if ap != 0:
               # U(1) < N(U(1)) :
               chars = symmetric_power_recursion(psi0,ap/RR(p).sqrt(),n-1)
               chars = [1,1] + chars[1:]
           else:
               # N(U(1))\U(1):
               chars = [1,-1] + [0 for i in range(n-2)]
        else:
           chars = symmetric_power_recursion(psi0,ap/RR(p).sqrt(),n)
        A += MatRR([[chars[i]*chars[j] for j in range(n)] for i in range(n)])
        num += 1
    return 1/num*A

In [3]:
E1 = EllipticCurve([0,-1,1,-10,-20])                                                                     

In [4]:
# E1: Generic elliptic curve of conductor 11:
A1 = elliptic_chars_matrix(E1,5)
print("Inner product matrix of SU(2) irreducible characters for E1:\n%s" % A1)
print("Approximating:")
print(matrix([ [ round(A1[i,j]) for j in range(5) ] for i in range(5) ]))

Inner product matrix of SU(2) irreducible characters for E1:
[   1.00000000 0.00480343155 -0.0331592300 0.00885968073 -0.0205551784]
[0.00480343155   0.966840769  0.0136631124 -0.0537144082  0.0205506508]
[-0.0331592300  0.0136631124   0.946285593  0.0253540824 -0.0257573944]
[0.00885968073 -0.0537144082  0.0253540824   0.974242606 -0.0336468926]
[-0.0205551784  0.0205506508 -0.0257573944 -0.0336468926    1.00271966]
Approximating:
[1 0 0 0 0]
[0 1 0 0 0]
[0 0 1 0 0]
[0 0 0 1 0]
[0 0 0 0 1]
